## The Encoder


## Self-Attention


In [ ]:
!pip install transformers
!pip install bertviz

In [2]:
from transformers import AutoTokenizer, AutoConfig, AutoModel
from bertviz.transformers_neuron_view import BertModel
from bertviz.neuron_view import show

from torch import nn
import torch
from math import sqrt
import torch.nn.functional as F

from bertviz import head_view

### Scaled dot-product attention


In [63]:
model_name = "bert-base-uncased"
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = BertModel.from_pretrained(model_name)

In [64]:
text = "Hello, my name is Titi, I am from France"
show(model, "bert",tokenizer,text,display_mode="light",layer=0,head=8)

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [65]:
inputs = tokenizer(text, return_tensors="pt", add_special_tokens=False)
inputs.input_ids

tensor([[ 7592,  1010,  2026,  2171,  2003, 14841,  3775,  1010,  1045,  2572,
          2013,  2605]])

In [66]:
config = AutoConfig.from_pretrained(model_name)
token_emb = nn.Embedding(config.vocab_size, config.hidden_size)
token_emb

Embedding(30522, 768)

In [67]:
inputs_embeds = token_emb(inputs.input_ids)
print(inputs_embeds.size(),"([batch_size, seq_len, hidden_dim])")

torch.Size([1, 12, 768]) ([batch_size, seq_len, hidden_dim])


In [68]:
def scaled_dot_product_attention(query,key,value):
  dim_k = query.size(-1)
  scores = torch.bmm(query, key.transpose(1,2)) / sqrt(dim_k)
  weights = F.softmax(scores, dim=1)
  return torch.bmm(weights, value)

In [69]:
class AttentionHead(nn.Module):
  def __init__(self, embed_dim, head_dim):
    super().__init__()
    self.q = nn.Linear(embed_dim, head_dim)
    self.k = nn.Linear(embed_dim, head_dim)
    self.v = nn.Linear(embed_dim, head_dim)

  def forward(self, hidden_state):
    attention_outputs = scaled_dot_product_attention(self.q(hidden_state), self.k(hidden_state), self.v(hidden_state))
    return attention_outputs




### Multi-headed attention

In [70]:
class MultiHeadAttention(nn.Module):
  def __init__(self,config):
    super().__init__()
    embed_dim = config.hidden_size
    num_heads = config.num_attention_heads
    head_dim = embed_dim // num_heads
    self.heads = nn.ModuleList([AttentionHead(embed_dim,head_dim) for _ in range(num_heads)])
    self.output_linear = nn.Linear(embed_dim, embed_dim)

  def forward(self, hidden_state):
      x= torch.cat([h(hidden_state) for h in self.heads], dim=-1)
      x= self.output_linear(x)
      return x

In [71]:
multihead_attention = MultiHeadAttention(config)
attention_output = multihead_attention(inputs_embeds)
attention_output.size()

torch.Size([1, 12, 768])

In [72]:
model = AutoModel.from_pretrained(model_name,output_attentions=True)

sentence_a = "time flies like an arrow"
sentence_b = "fruit flies like a banana"

viz_inputs = tokenizer(sentence_a, sentence_b, return_tensors="pt")
attention = model(**viz_inputs).attentions
sentence_b_start = (viz_inputs.token_type_ids == 0).sum(dim=1)
tokens = tokenizer.convert_ids_to_tokens(viz_inputs.input_ids[0])

head_view(attention, tokens, sentence_b_start, heads=[8])

<IPython.core.display.Javascript object>

## Feed-Forward Layer

In [73]:
class FeedForward(nn.Module):
  def __init__(self,config):
    super().__init__()
    self.linear_1 = nn.Linear(config.hidden_size, config.intermediate_size)
    self.linear_2 = nn.Linear(config.intermediate_size, config.hidden_size)
    self.gelu = nn.GELU()
    self.dropout = nn.Dropout(config.hidden_dropout_prob)

  def forward(self,x):
      x = self.linear_1(x)
      x= self.gelu(x)
      x = self.linear_2(x)
      x = self.dropout(x)
      return x

In [74]:
feed_forward = FeedForward(config)

ff_outputs = feed_forward(attention_output)
ff_outputs.size()

torch.Size([1, 12, 768])

## Adding Layer Normalization


In [75]:
class TransformerEncoderLayer(nn.Module):
  def __init__(self,config):
    super().__init__()
    self.layer_norm_1 = nn.LayerNorm(config.hidden_size)
    self.layer_norm_2 = nn.LayerNorm(config.hidden_size)
    self.attention = MultiHeadAttention(config)
    self.feed_forward = FeedForward(config)

  def forward(self,x):
      # Apply layer normalization and then copy input into query, key, value
      hidden_state = self.layer_norm_1(x)
      # Apply attention with a skip connection
      x = x + self.attention(hidden_state)
      # Apply feed-forward layer with a skip connection
      x = x + self.feed_forward(self.layer_norm_2(x))
      return x

In [76]:
encoder_layer = TransformerEncoderLayer(config)
inputs_embeds.shape, encoder_layer(inputs_embeds).size()

(torch.Size([1, 12, 768]), torch.Size([1, 12, 768]))

## Positional Embeddings

In [77]:
class Embeddings(nn.Module):
  def __init__(self,config):
    super().__init__()
    self.token_embeddings = nn.Embedding(config.vocab_size, config.hidden_size)
    self.position_embeddings = nn.Embedding(config.max_position_embeddings, config.hidden_size)
    self.layer_norm = nn.LayerNorm(config.hidden_size, eps=1e-12)
    self.dropout = nn.Dropout()

  def forward(self, input_ids):
    # Create position IDs for input sequence
    seq_length=input_ids.size(1)
    position_ids = torch.arange(seq_length, dtype=torch.long).unsqueeze(0)
    # Create token and position embeddings
    token_embeddings = self.token_embeddings(input_ids)
    position_embeddings = self.position_embeddings(position_ids)
    # Combine token and position embeddings
    embeddings = token_embeddings + position_embeddings
    embeddings = self.layer_norm(embeddings)
    embeddings = self.dropout(embeddings)
    return embeddings


In [78]:
embedding_layer = Embeddings(config)
embedding_layer(inputs.input_ids).size()

torch.Size([1, 12, 768])

## Full transformer encoder

In [79]:
class TransformerEncoder(nn.Module):
  def __init__(self,config):
    super().__init__()
    self.embeddings = Embeddings(config)
    self.layers=nn.ModuleList([TransformerEncoderLayer(config) for _ in range(config.num_hidden_layers)])

  def forward(self, x):
      x = self.embeddings(x)
      for layer in self.layers:
        x=layer(x)
      return x

In [80]:
encoder = TransformerEncoder(config)
encoder(inputs.input_ids).size()

torch.Size([1, 12, 768])